05.05.2021 - Modified - Loop
- Add new method to get th_resp
  - using median of resp
  - using center value of min and max of resp ((max - min) /2))

In [1]:
# #Display full output
# from IPython.core.interactiveshell import InteractiveShell
# InteractiveShell.ast_node_interactivity = "all"
from tqdm.auto import tqdm, trange
from ipywidgets import IntProgress
from IPython.display import display
from IPython.core.display import display, HTML
display(HTML("<style>div.output_scroll { height: 40em; }</style>"))

import warnings
warnings.filterwarnings('ignore')
import datetime
import time
from pytictoc import TicToc
import sys
import numpy as np
import pandas as pd
from sklearn.cluster import KMeans, MeanShift
from fcmeans import FCM
from sklearn.mixture import GaussianMixture
from sklearn.mixture_mod import GaussianMixtureMod
from sklearn.mixture_mod2 import GaussianMixtureMod2
from sklearn.mixture_mod3 import GaussianMixtureMod3
from sklearn.mixture_mod4 import GaussianMixtureMod4
from sklearn.mixture_mod5 import GaussianMixtureMod5
from IPython.utils import io
import numpy as np
from sklearn import metrics
from scipy.optimize import linear_sum_assignment
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, adjusted_rand_score, normalized_mutual_info_score, homogeneity_completeness_v_measure,fowlkes_mallows_score,silhouette_score
from sklearn.metrics import davies_bouldin_score, v_measure_score
from scipy.stats import chi2

#Funtion declaration
def cluster_accuracy(y_true, y_pred):
    # compute contingency matrix (also called confusion matrix)
    contingency_matrix = metrics.cluster.contingency_matrix(y_true, y_pred)
#     print("\ncontingency_matrix : \n", contingency_matrix)

    # Find optimal one-to-one mapping between cluster labels and true labels
    row_ind, col_ind = linear_sum_assignment(-contingency_matrix)
    print("row_ind : ", row_ind)
    print("col_ind : ", col_ind)
    val1 = contingency_matrix[row_ind, col_ind].sum()
    print("contingency_matrix[row_ind, col_ind].sum() : ", val1)
    val2 = np.sum(contingency_matrix)
    print("np.sum(contingency_matrix) : ", val2)

    # Return cluster accuracy
    return contingency_matrix[row_ind, col_ind].sum() / np.sum(contingency_matrix)

def purity_score(y_true, y_pred):
    # compute contingency matrix (also called confusion matrix)
    contingency_matrix = metrics.cluster.contingency_matrix(y_true, y_pred)
#     print("\ncontingency_matrix : \n", contingency_matrix)
    
    # return purity
    return np.sum(np.amax(contingency_matrix, axis=0)) / np.sum(contingency_matrix) 

#Get the Clustering Algorithm Performance
def cluster_eval(y_true, y_pred, X_train, cluster_label, m, elapsed_time,iter_num):
    eval_scores = []
    
    accuracy = np.mean(y_pred.ravel() == y_true.ravel()) * 100
    purity = purity_score(y_train, y_pred)
    micro_f1_score = f1_score(y_true, y_pred, average='micro')
    macro_f1_score = f1_score(y_true, y_pred, average='macro')
    weighted_f1_score = f1_score(y_true, y_pred, average='weighted')
    ari_score = adjusted_rand_score(y_true, y_pred)
    nmi_score = normalized_mutual_info_score(y_true, y_pred)
#     hc_v_measure = homogeneity_completeness_v_measure(y_true, y_pred)
    v_measure = v_measure_score(y_true, y_pred)
    fm_score = fowlkes_mallows_score(y_true, y_pred)
#     s_score = silhouette_score(X_train, y_pred, metric='euclidean')
#     db_score = davies_bouldin_score(X_train, y_pred)
    eval_scores = [m, cluster_label, elapsed_time, iter_num, accuracy, purity, micro_f1_score, macro_f1_score, weighted_f1_score, ari_score, 
                   nmi_score, v_measure, fm_score]
    return eval_scores

#function to remove outliers using z-score
def z_score(data):
    data_z = data['mean']
    outliers_z = data_z.copy()
    mean_z = np.mean(data_z)
    std_z =np.std(data_z)
    threshold=3.

    data['z_score'] = (outliers_z - mean_z)/std_z 
    outliers_z[(data['z_score'] > threshold)] = np.nan
    print('outliers_z : \n', outliers_z)
    #Drop outliers
    no_outliers_z = outliers_z.dropna()
    print('outliers_z_new : \n', no_outliers_z)    
    return no_outliers_z

#function to calculate means 
def means_init(X, n_components):
    n_samples, n_attributes = X.shape
    print("n_components : ", n_components)
    
    df_X = pd.DataFrame(X)
    
    df_X['mean'] = df_X.mean(axis=1)
    
    no_outliers_z = z_score(df_X)

    #Find Max, Min, Diff, Dev
    Max = max(no_outliers_z)
    Min = min(no_outliers_z)
    
    diff = Max - Min
    dev = diff/n_components
    
    print('Max: ', Max , 'Min: ', Min)   
    print('dev :', dev)
    
    cluster_range = np.zeros((n_components, 2))
    for i in range (n_components):
        cluster_range[i] = Min, Min+dev
        
        Min = Min+dev
        df_X['c'+str(i)]=0
    print(cluster_range)  

    for j in range (n_components):
        df_X['c'+str(j)][(df_X['mean']>= cluster_range[j,0]) & (df_X['mean'] < cluster_range[j,1])] = 1

    es_init_means = np.zeros((n_components, n_attributes))
    for k in range (n_components):    
        temp_df_X = df_X.iloc[:, 0:n_attributes][df_X['c'+str(k)] == 1]   
        es_init_means[k] = temp_df_X.mean(axis=0) 
    return es_init_means
"""------------------------------------------------------------------------------------------------------------------------
#Main Program - Start here!
------------------------------------------------------------------------------------------------------------------------"""
# np.set_printoptions(threshold=sys.maxsize)
# pd.set_option('display.max_rows', dataset.shape[0]+1)

#Define dataset_labels
# dataset_labels = ["iris",  "transfusion"]
# dataset_labels = ["heartDisease",  "transfusion", "wilt", "balanceScale","dermatology"]  
# # dataset_labels = ["transfusion", "wilt", "breastCancer", "heartDisease", "eegEyeState", "adultIncome",
#                   "australian", "japanese", "bank", "seismicBumps", "german", "chess", 
#                   "iris", "abalone", "wallRobot", "dermatology"]
                   
# dataset_labels = ["heartDisease", "transfusion", "wilt", "breastCancer", "chess", 
#                   "parkinson","australian", "german", "japanese", "iris", "abalone", "wallRobot",
#                   "dermatology","creditApproval", "letters", "eegEyeState",
#                   "seismicBumps","bank", "adultIncome", "sensorlessDrive"]
# dataset_labels = [ "transfusion", "wilt", "breastCancer", "heartDisease", "eegEyeState", "adultIncome",
#                   "australian", "japanese", "bank","german", "iris", "abalone",  "dermatology"]
# dataset_labels = ["transfusion", "wilt", "breastCancer", "heartDisease", "eegEyeState", "adultIncome",
#                   "australian", "japanese", "bank", "seismicBumps", "german", "chess", 
#                   "iris", "abalone", "wallRobot", "dermatology"]
# dataset_labels = ["transfusion", "wilt", "breastCancer", "heartDisease","adultIncome",
#                   "australian", "japanese", "bank", "seismicBumps", "german", "chess", 
#                   "iris", "abalone", "wallRobot", "dermatology"]
# dataset_labels = ["transfusion", "wilt", "breastCancer", "heartDisease","adultIncome"]
dataset_labels = ["iris"]
skip_Mahal = ["australian","japanese", "seismicBumps","bank", "adultIncome"]

# cov_type_labels = ["full", "tied", "diag", "spherical"]
cov_type_labels = ["full", "tied"]
# Threshold of GMM-EM Response values
th_resp_val = [0.1, 0.2, 0.3, 0.4, 0.5]
# th_resp_val = [1]

# resp_type_val = ['remove']
# resp_type_val = ['donate']
resp_type_val = ['remove', 'donate']

result_labels = ["Dataset","Algorithm", "Elapsed Time", "Iter_num","accuracy", "purity", "micro_f1_score", "macro_f1_score", "weighted_f1_score", "ari_score", 
                "nmi_score", "hc_v_measure", "fm_score"]
for repeat in range (10):
    for cov_type in (cov_type_labels):
        print("\nStart Cov_Type :",cov_type)

        all_scores = []
        final_scores = []
        all_result = pd.DataFrame()
        t = TicToc() # create TicToc instance
        # for m in dataset_labels:
        for m in tqdm(dataset_labels):
        #     enablePrint()
            print("\n\nStart Dataset : ",m)
            #Read dataset
            dataset = pd.read_csv("dataset/"+m+".csv")

            #Drop Target Column in data using Index
            X_train = dataset.drop('Target',axis=1)

            # #How to get Target data
            y_train =  dataset['Target']

            print(np.array(y_train))

            n_classes = len(np.unique(y_train))

            #     cov_type = 'full'
        #     cov_type = 'full'
        #     cov_type = 'diag'
            #Since we have class labels for the training data, we can initialize the GMM parameters in a supervised manner.
        #     es_means_init = np.array([X_train[y_train == i].mean(axis=0) for i in range(n_classes)])

        #     es_means_init = np.array ([[5.005555556, 3.344444444, 1.596296296, 0.303703704],
        #                                 [5.973333333, 2.775, 4.503333333, 1.468333333],
        #                                 [6.86, 3.077142857, 5.731428571, 2.091428571]]) 
            X = X_train.copy()
            es_means_init = means_init(X, n_classes)
            print("es_means_init :\n",es_means_init)
            if (m == "wilt"):
        #         es_means_init[[0, 1]] = es_means_init[[1, 0]] 
                print("es_means_init_"+m+" :\n",es_means_init) 
            elif (m == "heartDisease"):
                es_means_init[[0, 1]] = es_means_init[[1, 0]] 
                print("es_means_init_"+m+" :\n",es_means_init) 
            elif (m == "adultIncome"):
                es_means_init[[0, 1]] = es_means_init[[1, 0]] 
                print("es_means_init_"+m+" :\n",es_means_init) 
            elif (m == "australian"):
                es_means_init[[0, 1]] = es_means_init[[1, 0]] 
                print("es_means_init_"+m+" :\n",es_means_init)   
            elif (m == "wallRobot"):
                es_means_init[[0, 1, 2, 3]] = es_means_init[[1, 2, 3, 0]] 
                print("es_means_init_"+m+" :\n",es_means_init)     
            elif (m == "dermatology"):
                es_means_init[[0, 1, 2, 3, 4, 5]] = es_means_init[[3, 5, 4, 1, 0, 2]] 
                print("es_means_init_"+m+" :\n",es_means_init) 
        #     es_means_init = None

            #Run the kMeans on current
            kMeans_cluster = KMeans(n_clusters = n_classes, max_iter=20, random_state=0)
            t.tic() # Start timer
            kMeans_cluster.fit(X_train)
            elapsed_time = t.tocvalue() #Save elapsed time
            iter_num = kMeans_cluster.n_iter_
        #     print("kMeans time : ", elapsed_time )   
            y_train_pred = kMeans_cluster.predict(X_train)
            eval_scores = cluster_eval(y_train, y_train_pred, X_train, "kMeans", m, elapsed_time, iter_num )
        #     eval_scores = np.append([m],eval_scores,axis=0)  
            all_scores = [eval_scores]

        #     #Run the Meanshift on current
        #     ms_cluster = MeanShift(bandwidth=n_classes)
        #     t.tic() # Start timer
        #     ms_cluster = ms_cluster.fit(X_train)
        #     elapsed_time = t.tocvalue() #Save elapsed time
        #     iter_num = "NA" #ms_cluster.n_iter_
        # #     print("GMM time : ", elapsed_time )       
        #     y_train_pred = ms_cluster.predict(X_train)
        #     eval_scores = cluster_eval(y_train, y_train_pred, X_train, "Meanshift", m, elapsed_time, iter_num )
        # #     all_scores += [eval_scores]
        #     all_scores += [eval_scores]

        #     #Run the FCM on current
        #     fcm_cluster = FCM(n_clusters=n_classes)
        #     t.tic() # Start timer
        #     fcm_cluster.fit(X_train)
        #     elapsed_time = t.tocvalue() #Save elapsed time
        #     iter_num = "NA" #fcm_cluster.n_iter_
        # #     print("GMM time : ", elapsed_time )       
        #     y_train_pred = fcm_cluster.predict(X_train)
        #     eval_scores = cluster_eval(y_train, y_train_pred, X_train, "FCM", m, elapsed_time, iter_num )
        # #     all_scores += [eval_scores]
        #     all_scores += [eval_scores]

            #Run the GMM on current
            gmm_cluster = GaussianMixture(n_components = n_classes, init_params='random', means_init= None, covariance_type=cov_type, max_iter=20, random_state=0)
            t.tic() # Start timer
            gmm_cluster.fit(X_train)
            elapsed_time = t.tocvalue() #Save elapsed time
            iter_num = gmm_cluster.n_iter_
        #     print("GMM time : ", elapsed_time )       
            y_train_pred = gmm_cluster.predict(X_train)
            eval_scores = cluster_eval(y_train, y_train_pred, X_train, "GMM-random", m, elapsed_time, iter_num )
        #     all_scores += [eval_scores]
            all_scores += [eval_scores]

                    #Run the GMM on current
            gmm_cluster = GaussianMixture(n_components = n_classes, init_params='kmeans', means_init= None, covariance_type=cov_type, max_iter=20, random_state=0)
            t.tic() # Start timer
            gmm_cluster.fit(X_train)
            elapsed_time = t.tocvalue() #Save elapsed time
            iter_num = gmm_cluster.n_iter_
        #     print("GMM time : ", elapsed_time )       
            y_train_pred = gmm_cluster.predict(X_train)
            eval_scores = cluster_eval(y_train, y_train_pred, X_train, "GMM-kmeans", m, elapsed_time, iter_num )
        #     all_scores += [eval_scores]
            all_scores += [eval_scores]

             #Run the GMM on current
            gmm_cluster = GaussianMixture(n_components = n_classes, init_params='jaha_init', means_init= None, covariance_type=cov_type, max_iter=20, random_state=0)
            t.tic() # Start timer
            gmm_cluster.fit(X_train)
            elapsed_time = t.tocvalue() #Save elapsed time
            iter_num = gmm_cluster.n_iter_
        #     print("GMM time : ", elapsed_time )       
            y_train_pred = gmm_cluster.predict(X_train)
            eval_scores = cluster_eval(y_train, y_train_pred, X_train, "GMM-jaha_init", m, elapsed_time, iter_num )
        #     all_scores += [eval_scores]
            all_scores += [eval_scores]

        #     #Run the GMM Mahalanobis on current - Last tested on 28.01.2021
        #     if m not in (skip_Mahal):    
        #         for resp_type in resp_type_val:
        #             gmm_cluster_mod2 = GaussianMixtureMod2(n_components = n_classes, init_params='kmeans', means_init=None, covariance_type=cov_type, max_iter=20, random_state=0, resp_type=resp_type)
        #             t.tic() # Start timer
        #             gmm_cluster_mod2.fit(X_train)
        #             elapsed_time = t.tocvalue() #Save elapsed time
        #             iter_num = gmm_cluster_mod2.n_iter_
        #         #     print("GMM time : ", elapsed_time ) 
        #             resp_labels = "Mahalanobis-"+str(resp_type)
        #             y_train_pred_mod2 = gmm_cluster_mod2.predict(X_train)
        #             eval_scores = cluster_eval(y_train, y_train_pred_mod2, X_train, resp_labels, m, elapsed_time, iter_num )
        #             all_scores += [eval_scores]
        #         print("Finish GaussianMixtureMod2/Mahalanobis : ",m," : ",resp_type )
        #     else:
        #         print("Skip GaussianMixtureMod2/Mahalanobis for :",m )

            # Run the GMM-Auto for every th_resp value on current dataset (using intersect)- Last tested on 27.01.2021
            #     for resp_type in resp_type_val:
            #         gmm_cluster_mod3 = GaussianMixtureMod3(n_components=n_classes, init_params='random', means_init=es_means_init, covariance_type=cov_type, max_iter=20, random_state=0, resp_type=resp_type )
            #         t.tic() # Start timer
            #         gmm_cluster_mod3.fit(X_train)
            #         elapsed_time = t.tocvalue() #Save elapsed time
            #         iter_num = gmm_cluster_mod3.n_iter_     
            #         resp_labels = "GMM_Auto-"+str(resp_type)
            #         y_train_pred_mod3 = gmm_cluster_mod3.predict(X_train)
            #         eval_scores = cluster_eval(y_train, y_train_pred_mod3, X_train, resp_labels,m, elapsed_time, iter_num)
            #         all_scores += [eval_scores]
            #     print("Finish GaussianMixtureMod3 : ", m," : ",resp_type )

            #Run the GMM-Auto-v2 for every th_resp value on current dataset (using weights*cv or cv/2) - Last tested on 27.01.2021
            for resp_type in resp_type_val:
                gmm_cluster_mod4 = GaussianMixtureMod4(n_components=n_classes, init_params='jaha_init', means_init=None, covariance_type=cov_type, max_iter=20, random_state=0, resp_type=resp_type )
                t.tic() # Start timer
                gmm_cluster_mod4.fit(X_train)
                elapsed_time = t.tocvalue() #Save elapsed time
                iter_num = gmm_cluster_mod4.n_iter_     
                resp_labels = "resp Mixing Coefficients -"+str(resp_type)
                y_train_pred_mod4 = gmm_cluster_mod4.predict(X_train)
                eval_scores = cluster_eval(y_train, y_train_pred_mod4, X_train, resp_labels,m, elapsed_time, iter_num)
                all_scores += [eval_scores]
            print("Finish GaussianMixtureMod4/resp Mixing Coefficients  : ", m, " : ",resp_type )

            #Run the GMM-Auto-v2 for every th_resp value on current dataset (using resp center values) - Last tested on 27.01.2021
            for resp_type in resp_type_val:
                gmm_cluster_mod5 = GaussianMixtureMod5(n_components=n_classes, init_params='jaha_init', means_init=None, covariance_type=cov_type, max_iter=20, random_state=0, resp_type=resp_type )
                t.tic() # Start timer
                gmm_cluster_mod5.fit(X_train)
                elapsed_time = t.tocvalue() #Save elapsed time
                iter_num = gmm_cluster_mod5.n_iter_     
                resp_labels = "resp center values-"+str(resp_type)
                y_train_pred_mod5 = gmm_cluster_mod5.predict(X_train)
                eval_scores = cluster_eval(y_train, y_train_pred_mod5, X_train, resp_labels,m, elapsed_time, iter_num)
                all_scores += [eval_scores]
            print("Finish GaussianMixtureMod5/resp center values : ", m, " : ",resp_type )

        #     #Run the GMM-OR for every th_resp value on current dataset
        #     for resp_type in resp_type_val:
        #         for th_resp in th_resp_val:
        #             gmm_cluster_mod = GaussianMixtureMod(n_components=n_classes, init_params='random', means_init=es_means_init, covariance_type=cov_type, max_iter=20, random_state=0, th_resp=th_resp, resp_type=resp_type )

        #             t.tic() # Start timer
        #             gmm_cluster_mod.fit(X_train)
        #             elapsed_time = t.tocvalue() #Save elapsed time
        #             iter_num = gmm_cluster_mod.n_iter_       
        #             y_train_pred_mod = gmm_cluster_mod.predict(X_train)
        #             th_resp_labels = "GMM-"+str(resp_type)+"_th_resp="+str(th_resp)
        #     #         print(th_resp_labels," time : ", elapsed_time )   
        #             eval_scores = cluster_eval(y_train, y_train_pred_mod, X_train, th_resp_labels,m, elapsed_time, iter_num)
        #             all_scores += [eval_scores]

            #Change result to Pandas DataFrame
            result = pd.DataFrame(all_scores)
            all_result = all_result.append(result)
            print("Finish GaussianMixtureMod : ", m, " : ",resp_type )
        all_result = all_result.append(pd.Series(), ignore_index=True) 
        all_result.columns=result_labels    


        #Save results to Excel
        ts = time.time() 
        st = datetime.datetime.fromtimestamp(ts).strftime('%H-%M-%S---%d-%m-%Y')
        # all_result.to_excel("result/All_result_"+st+".xlsx", index=False)
        all_result.to_excel("result/loop/All_result_"+str(repeat)+"_"+cov_type+"_"+st+".xlsx", index=False)
print("\nFinish at ",st)



Start Cov_Type : full




Start Dataset :  transfusion
[1 1 1 1 0 0 1 0 1 1 0 0 1 0 1 1 1 1 1 1 1 0 1 1 0 0 0 1 1 0 0 1 1 1 0 1 1
 1 1 1 1 0 1 0 1 1 0 0 0 0 0 1 0 0 1 1 1 1 0 0 0 1 0 1 1 0 1 0 0 0 0 0 1 0
 1 1 1 0 0 0 1 0 0 0 1 0 0 0 0 1 1 0 0 0 0 0 0 1 1 1 1 1 0 0 0 0 0 0 0 0 1
 0 0 1 0 0 1 0 0 1 1 1 1 1 0 0 1 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 0 0
 1 0 1 0 0 1 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 0 0 0 0
 0 0 0 0 1 0 0 0 0 0 1 1 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 1
 1 0 1 1 0 0 0 0 0 1 0 0 0 0 0 0 0 0 1 0 1 1 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0
 0 0 1 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 1 1 1 1 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 0 1 0 0 0 0 1 0 0 0 1
 1 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1
 1 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 1 0 0 0 0 0 0 1 0 0 

Name: 0, Length: 748, dtype: float64
0      0.0
1      0.0
2      0.0
3      0.0
4      0.0
      ... 
743    0.0
744    0.0
745    0.0
746    0.0
747    0.0
Name: 1, Length: 748, dtype: float64
Inside jaha_utils
resp in jaha_init mod4:
  [[0. 0.]
 [0. 1.]
 [0. 1.]
 ...
 [1. 0.]
 [1. 0.]
 [1. 0.]]

In _initialize_parameters , base.py

In _initialize , gaussian_mixture_mod4.py
Start of iteration :  1
Start Donate :  1

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  1
Start of iteration :  2
Start Donate :  2

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  2
Start of iteration :  3
Start Donate :  3

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  3
Start of iteration :  4
Start Donate :  4

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  4
Start of iteration :  5
Start Donate :  5

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of i

In _estimate_gaussian_parameters_em, gaussian_mixture_mod5.py
End of iteration :  11
log_prob_norm : -9.780212007047599
lower_bound : -9.780212007047599
prev_lower_bound : -9.792950586670488
change : 0.012738579622888935
Start of iteration :  12
th_resp : [0.5 0.5]
self.weights_ : th_resp  in m_step  [0.60583059 0.39416941]  :  [0.5 0.5]
Start Donate :  12

In _estimate_gaussian_parameters_em, gaussian_mixture_mod5.py
End of iteration :  12
log_prob_norm : -9.771105813539023
lower_bound : -9.771105813539023
prev_lower_bound : -9.780212007047599
change : 0.009106193508575444
Start of iteration :  13
th_resp : [0.5 0.5]
self.weights_ : th_resp  in m_step  [0.58766328 0.41233672]  :  [0.5 0.5]
Start Donate :  13

In _estimate_gaussian_parameters_em, gaussian_mixture_mod5.py
End of iteration :  13
log_prob_norm : -9.767565698523935
lower_bound : -9.767565698523935
prev_lower_bound : -9.771105813539023
change : 0.003540115015088219
Start of iteration :  14
th_resp : [0.5 0.5]
self.weights_ 

th_resp : [0.5 0.5]
self.weights_ : th_resp  in m_step  [0.81543579 0.18456421]  :  [0.5 0.5]

In _estimate_gaussian_parameters_em, gaussian_mixture_mod5.py
End of iteration :  9
log_prob_norm : -22.214416526386845
lower_bound : -22.214416526386845
prev_lower_bound : -22.217200693083836
change : 0.002784166696990553
Start of iteration :  10
th_resp : [0.5 0.5]
self.weights_ : th_resp  in m_step  [0.80882124 0.19117876]  :  [0.5 0.5]

In _estimate_gaussian_parameters_em, gaussian_mixture_mod5.py
End of iteration :  10
log_prob_norm : -22.213297110749952
lower_bound : -22.213297110749952
prev_lower_bound : -22.214416526386845
change : 0.0011194156368929953
Start of iteration :  11
th_resp : [0.5 0.5]
self.weights_ : th_resp  in m_step  [0.80397419 0.19602581]  :  [0.5 0.5]

In _estimate_gaussian_parameters_em, gaussian_mixture_mod5.py
End of iteration :  11
log_prob_norm : -22.213019182786834
lower_bound : -22.213019182786834
prev_lower_bound : -22.213297110749952
change : 0.000277927963

...

 [0. 0.]]
       0    1
0    0.0  0.0
1    0.0  0.0
2    0.0  0.0
3    0.0  0.0
4    0.0  0.0
..   ...  ...
298  0.0  0.0
299  0.0  0.0
300  0.0  0.0
301  0.0  0.0
302  0.0  0.0

[303 rows x 2 columns]
Max:  58.3 Min:  33.76923076923077
dev : 12.265384615384615
[[33.76923077 46.03461538]
 [46.03461538 58.3       ]]
0      0.0
1      0.0
2      0.0
3      0.0
4      0.0
      ... 
298    0.0
299    0.0
300    0.0
301    0.0
302    0.0
Name: 0, Length: 303, dtype: float64
0      0.0
1      0.0
2      0.0
3      0.0
4      0.0
      ... 
298    0.0
299    0.0
300    0.0
301    0.0
302    0.0
Name: 1, Length: 303, dtype: float64
Inside jaha_utils
resp in jaha_init mixture :
  [[0. 1.]
 [0. 1.]
 [1. 0.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [0. 1.]
 [0. 1.]
 [1. 0.]
 [1. 0.]
 [0. 1.]
 [0. 1.]
 [0. 1.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [0. 1.]
 [0. 1.]
 [1. 0.]
 [1. 0.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [1. 0.]
 [0. 0.]
 [1. 0.]
 [1. 0.]
 [1. 0.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [1.

 [0. 1.]]

In _initialize_parameters , base.py

In _initialize , gaussian_mixture_mod4.py
Start of iteration :  1

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  1
Start of iteration :  2

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  2
Start of iteration :  3

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  3
Start of iteration :  4

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  4
Start of iteration :  5

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  5
Start of iteration :  6

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  6
Start of iteration :  7

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  7
Start of iteration :  8

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  8
Start of iteration :  9

In _estimate_

 [0. 1.]]

In _initialize_parameters , base.py

In _initialize , gaussian_mixture_mod4.py
Start of iteration :  1
Start Donate :  1

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  1
Start of iteration :  2
Start Donate :  2

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  2
Start of iteration :  3
Start Donate :  3

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  3
Start of iteration :  4
Start Donate :  4

In _estimate_gaussian_parameters_em, gaussian_mixture_mod4.py
End of iteration :  4
Num of Iteration :  4
Finish of th_resp :  1
Finish GaussianMixtureMod4/resp Mixing Coefficients  :  heartDisease  :  donate

In __init__ , base.py

In __init__ , gaussian_mixture_mod5 class in gaussian_mixturem_mod5.py

In fit , base.py

In fit_predict , base.py
n_components :  2
outliers_z : 
 0      46.100000
1      47.192308
2      42.569231
3      45.984615
4      53.892308
         ...    
298

 [0. 0.]]
       0    1
0    0.0  0.0
1    0.0  0.0
2    0.0  0.0
3    0.0  0.0
4    0.0  0.0
..   ...  ...
298  0.0  0.0
299  0.0  0.0
300  0.0  0.0
301  0.0  0.0
302  0.0  0.0

[303 rows x 2 columns]
Max:  58.3 Min:  33.76923076923077
dev : 12.265384615384615
[[33.76923077 46.03461538]
 [46.03461538 58.3       ]]
0      0.0
1      0.0
2      0.0
3      0.0
4      0.0
      ... 
298    0.0
299    0.0
300    0.0
301    0.0
302    0.0
Name: 0, Length: 303, dtype: float64
0      0.0
1      0.0
2      0.0
3      0.0
4      0.0
      ... 
298    0.0
299    0.0
300    0.0
301    0.0
302    0.0
Name: 1, Length: 303, dtype: float64
Inside jaha_utils
resp in jaha_init mod5:
  [[0. 1.]
 [0. 1.]
 [1. 0.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [0. 1.]
 [0. 1.]
 [1. 0.]
 [1. 0.]
 [0. 1.]
 [0. 1.]
 [0. 1.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [0. 1.]
 [0. 1.]
 [1. 0.]
 [1. 0.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [1. 0.]
 [0. 0.]
 [1. 0.]
 [1. 0.]
 [1. 0.]
 [1. 0.]
 [0. 1.]
 [1. 0.]
 [1. 0.]

Name: mean, Length: 48842, dtype: float64
[[0. 0.]
 [0. 0.]
 [0. 0.]
 ...
 [0. 0.]
 [0. 0.]
 [0. 0.]]
         0    1
0      0.0  0.0
1      0.0  0.0
2      0.0  0.0
3      0.0  0.0
4      0.0  0.0
...    ...  ...
48837  0.0  0.0
48838  0.0  0.0
48839  0.0  0.0
48840  0.0  0.0
48841  0.0  0.0

[48842 rows x 2 columns]
Max:  2052.8571428571427 Min:  6.785714285714286
dev : 1023.0357142857142
[[   6.78571429 1029.82142857]
 [1029.82142857 2052.85714286]]
0        0.0
1        0.0
2        0.0
3        0.0
4        0.0
        ... 
48837    0.0
48838    0.0
48839    0.0
48840    0.0
48841    0.0
Name: 0, Length: 48842, dtype: float64
0        0.0
1        0.0
2        0.0
3        0.0
4        0.0
        ... 
48837    0.0
48838    0.0
48839    0.0
48840    0.0
48841    0.0
Name: 1, Length: 48842, dtype: float64
Inside jaha_utils
resp in jaha_init mod5:
  [[0. 1.]
 [1. 0.]
 [0. 1.]
 ...
 [1. 0.]
 [0. 1.]
 [0. 1.]]

In _initialize_parameters , base.py

In _initialize , gaussian_mixture_mod

### End Here

In [ ]:
#Import functions from Local File "myfunc"
from ipynb.fs.full.jahaUtils import JahaInit

#function to calculate means 
def means_init(X, n_components):
    n_samples, n_attributes = X.shape
    print("n_components : ", n_components)
    
    df_X = pd.DataFrame(X)
    
    df_X['mean'] = df_X.mean(axis=1)
    
    no_outliers_z = z_score(df_X)
    
    resp = np.zeros((n_samples, n_components))
    print(resp)
    resp = pd.DataFrame(resp)
    print(resp)

    #Find Max, Min, Diff, Dev
    Max = max(no_outliers_z)
    Min = min(no_outliers_z)
    
    diff = Max - Min
    dev = diff/n_components
    
    print('Max: ', Max , 'Min: ', Min)   
    print('dev :', dev)
    
    cluster_range = np.zeros((n_components, 2))
    for i in range (n_components):
        cluster_range[i] = Min, Min+dev
        
        Min = Min+dev
        df_X['c'+str(i)]=0
        
        
    print(cluster_range)  
      
    for j in range (n_components):
        print(resp[j])
        resp[j][(df_X['mean']>= cluster_range[j,0]) & (df_X['mean'] < cluster_range[j,1])] = 1
        df_X['c'+str(j)][(df_X['mean']>= cluster_range[j,0]) & (df_X['mean'] < cluster_range[j,1])] = 1
        
    resp.to_excel("result/apr/resp.xlsx", index=False)
    df_X.to_excel("result/apr/df_X.xlsx", index=False)
    

    return es_init_means

dataset = pd.read_csv("dataset/iris.csv")

#Drop Target Column in data using Index
X = dataset.drop('Target',axis=1)

# #How to get Target data
y_train =  dataset['Target']

n_components = len(np.unique(y_train))
n_samples, _ = X.shape

resp = means_init(X, n_components)
# # if self.init_params == 'kmeans':
# resp = np.zeros((n_samples, n_components))
# # print(resp)
# label = KMeans(n_clusters=n_components, n_init=1, random_state=0).fit(X).labels_
# print(label)
# resp[np.arange(n_samples), label] = 1
# print(resp)

# resp = np.random.rand(n_samples, n_components)
# print(resp)
# print(resp.sum(axis=1)[:, np.newaxis])
# resp /= resp.sum(axis=1)[:, np.newaxis]
# print(resp)




In [ ]:
means = np.array ([[5.005555556, 3.344444444, 1.596296296, 0.303703704],
                        [5.973333333, 2.775, 4.503333333, 1.468333333],
                        [6.86, 3.077142857, 5.731428571, 2.091428571]]) 


print(means)

es_means_init :
 [[5.006 3.428 1.462 0.246]
 [5.936 2.77  4.26  1.326]
 [6.588 2.974 5.552 2.026]]

#Test Mahalanobis only 11.03.2021

In [ ]:
# #Display full output
# from IPython.core.interactiveshell import InteractiveShell
# InteractiveShell.ast_node_interactivity = "all"
from tqdm.auto import tqdm, trange
from ipywidgets import IntProgress
from IPython.display import display
from IPython.core.display import display, HTML
display(HTML("<style>div.output_scroll { height: 40em; }</style>"))

import warnings
warnings.filterwarnings('ignore')
import datetime
import time
from pytictoc import TicToc
import sys
import numpy as np
import pandas as pd
from sklearn.cluster import KMeans, MeanShift
from fcmeans import FCM
from sklearn.mixture import GaussianMixture
from sklearn.mixture_mod import GaussianMixtureMod
from sklearn.mixture_mod2 import GaussianMixtureMod2
from sklearn.mixture_mod3 import GaussianMixtureMod3
from sklearn.mixture_mod4 import GaussianMixtureMod4
from sklearn.mixture_mod5 import GaussianMixtureMod5
from IPython.utils import io
import numpy as np
from sklearn import metrics
from scipy.optimize import linear_sum_assignment
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, adjusted_rand_score, normalized_mutual_info_score, homogeneity_completeness_v_measure,fowlkes_mallows_score,silhouette_score
from sklearn.metrics import davies_bouldin_score, v_measure_score

#Funtion declaration
def cluster_accuracy(y_true, y_pred):
    # compute contingency matrix (also called confusion matrix)
    contingency_matrix = metrics.cluster.contingency_matrix(y_true, y_pred)
#     print("\ncontingency_matrix : \n", contingency_matrix)

    # Find optimal one-to-one mapping between cluster labels and true labels
    row_ind, col_ind = linear_sum_assignment(-contingency_matrix)
    print("row_ind : ", row_ind)
    print("col_ind : ", col_ind)
    val1 = contingency_matrix[row_ind, col_ind].sum()
    print("contingency_matrix[row_ind, col_ind].sum() : ", val1)
    val2 = np.sum(contingency_matrix)
    print("np.sum(contingency_matrix) : ", val2)

    # Return cluster accuracy
    return contingency_matrix[row_ind, col_ind].sum() / np.sum(contingency_matrix)

def purity_score(y_true, y_pred):
    # compute contingency matrix (also called confusion matrix)
    contingency_matrix = metrics.cluster.contingency_matrix(y_true, y_pred)
#     print("\ncontingency_matrix : \n", contingency_matrix)
    
    # return purity
    return np.sum(np.amax(contingency_matrix, axis=0)) / np.sum(contingency_matrix) 

#Get the Clustering Algorithm Performance
def cluster_eval(y_true, y_pred, X_train, cluster_label, m, elapsed_time,iter_num):
    eval_scores = []
    
    accuracy = np.mean(y_pred.ravel() == y_true.ravel()) * 100
    purity = purity_score(y_train, y_pred)
    micro_f1_score = f1_score(y_true, y_pred, average='micro')
    macro_f1_score = f1_score(y_true, y_pred, average='macro')
    weighted_f1_score = f1_score(y_true, y_pred, average='weighted')
    ari_score = adjusted_rand_score(y_true, y_pred)
    nmi_score = normalized_mutual_info_score(y_true, y_pred)
#     hc_v_measure = homogeneity_completeness_v_measure(y_true, y_pred)
    v_measure = v_measure_score(y_true, y_pred)
    fm_score = fowlkes_mallows_score(y_true, y_pred)
#     s_score = silhouette_score(X_train, y_pred, metric='euclidean')
#     db_score = davies_bouldin_score(X_train, y_pred)
    eval_scores = [m, cluster_label, elapsed_time, iter_num, accuracy, purity, micro_f1_score, macro_f1_score, weighted_f1_score, ari_score, 
                   nmi_score, v_measure, fm_score]
    return eval_scores
    
"""------------------------------------------------------------------------------------------------------------------------
#Main Program - Start here!
------------------------------------------------------------------------------------------------------------------------"""
# np.set_printoptions(threshold=sys.maxsize)
# pd.set_option('display.max_rows', dataset.shape[0]+1)

#Define dataset_labels
dataset_labels = ["iris"]
# dataset_labels = ["heartDisease",  "transfusion", "wilt", "balanceScale","dermatology"]  
# dataset_labels = ["heartDisease", "transfusion", "wilt", "breastCancer", "chess", 
#                   "parkinson","australian", "german", "japanese", "iris", "abalone", "wallRobot",
#                   "dermatology","creditApproval", "letters", "eegEyeState",
#                   "seismicBumps","bank", "adultIncome", "sensorlessDrive"]
#Final dataset tested on 11.03.2021
# dataset_labels = ["transfusion", "wilt", "breastCancer", "heartDisease", "eegEyeState", "adultIncome",
#                   "australian", "japanese", "bank", "seismicBumps", "german", "chess", 
#                   "iris", "abalone", "wallRobot", "dermatology"]
# dataset_labels = ["seismicBumps","bank", "adultIncome"]
# skip_Mahal = ["seismicBumps","bank", "adultIncome"]
skip_Mahal = ["seismicBumps","bank"]
# Threshold of GMM-EM Response values
th_resp_val = [0.1, 0.2, 0.3, 0.4, 0.5]
# th_resp_val = [1]

# resp_type_val = ['donate']
# resp_type_val = ['donate']
resp_type_val = ['remove', 'donate']

result_labels = ["Dataset","Algorithm", "Elapsed Time", "Iter_num","accuracy", "purity", "micro_f1_score", "macro_f1_score", "weighted_f1_score", "ari_score", 
                "nmi_score", "hc_v_measure", "fm_score"]

all_scores = []
final_scores = []
all_result = pd.DataFrame()
t = TicToc() # create TicToc instance
# for m in dataset_labels:
for m in tqdm(dataset_labels):
#     enablePrint()
    print("\n\nStart Dataset : ",m)
    #Read dataset
    dataset = pd.read_csv("dataset/"+m+".csv")

    #Drop Target Column in data using Index
    X_train = dataset.drop('Target',axis=1)

    # #How to get Target data
    y_train =  dataset['Target']

    print(np.array(y_train))

    n_classes = len(np.unique(y_train))
#     cov_type = 'full'
    cov_type = 'tied'
#     cov_type = 'diag'
    #Since we have class labels for the training data, we can initialize the GMM parameters in a supervised manner.
    es_means_init = np.array([X_train[y_train == i].mean(axis=0) for i in range(n_classes)])
#     print("es_means_init :\n",es_means_init)

    #Run the kMeans on current
    kMeans_cluster = KMeans(n_clusters = n_classes, max_iter=20, random_state=0)
    t.tic() # Start timer
    kMeans_cluster.fit(X_train)
    elapsed_time = t.tocvalue() #Save elapsed time
    iter_num = kMeans_cluster.n_iter_
#     print("kMeans time : ", elapsed_time )   
    y_train_pred = kMeans_cluster.predict(X_train)
    eval_scores = cluster_eval(y_train, y_train_pred, X_train, "kMeans", m, elapsed_time, iter_num )
#     eval_scores = np.append([m],eval_scores,axis=0)  
    all_scores = [eval_scores]
    
#     #Run the Meanshift on current
#     ms_cluster = MeanShift(bandwidth=n_classes)
#     t.tic() # Start timer
#     ms_cluster = ms_cluster.fit(X_train)
#     elapsed_time = t.tocvalue() #Save elapsed time
#     iter_num = "NA" #ms_cluster.n_iter_
# #     print("GMM time : ", elapsed_time )       
#     y_train_pred = ms_cluster.predict(X_train)
#     eval_scores = cluster_eval(y_train, y_train_pred, X_train, "Meanshift", m, elapsed_time, iter_num )
# #     all_scores += [eval_scores]
#     all_scores += [eval_scores]
    
#     #Run the FCM on current
#     fcm_cluster = FCM(n_clusters=n_classes)
#     t.tic() # Start timer
#     fcm_cluster.fit(X_train)
#     elapsed_time = t.tocvalue() #Save elapsed time
#     iter_num = "NA" #fcm_cluster.n_iter_
# #     print("GMM time : ", elapsed_time )       
#     y_train_pred = fcm_cluster.predict(X_train)
#     eval_scores = cluster_eval(y_train, y_train_pred, X_train, "FCM", m, elapsed_time, iter_num )
# #     all_scores += [eval_scores]
#     all_scores += [eval_scores]

    #Run the GMM on current
    gmm_cluster = GaussianMixture(n_components = n_classes, init_params='random', means_init=es_means_init, covariance_type=cov_type, max_iter=20, random_state=0)
    t.tic() # Start timer
    gmm_cluster.fit(X_train)
    elapsed_time = t.tocvalue() #Save elapsed time
    iter_num = gmm_cluster.n_iter_
#     print("GMM time : ", elapsed_time )       
    y_train_pred = gmm_cluster.predict(X_train)
    eval_scores = cluster_eval(y_train, y_train_pred, X_train, "GMM", m, elapsed_time, iter_num )
#     all_scores += [eval_scores]
    all_scores += [eval_scores]

    #Run the GMM Mahalanobis on current - Last tested on 28.01.2021
    if m not in (skip_Mahal):    
        for resp_type in resp_type_val:
            gmm_cluster_mod2 = GaussianMixtureMod2(n_components = n_classes, init_params='random', means_init=es_means_init, covariance_type=cov_type, max_iter=20, random_state=0, resp_type=resp_type)
            t.tic() # Start timer
            gmm_cluster_mod2.fit(X_train)
            elapsed_time = t.tocvalue() #Save elapsed time
            iter_num = gmm_cluster_mod2.n_iter_
        #     print("GMM time : ", elapsed_time ) 
            resp_labels = "Mahalanobis-"+str(resp_type)
            y_train_pred_mod2 = gmm_cluster_mod2.predict(X_train)
            eval_scores = cluster_eval(y_train, y_train_pred_mod2, X_train, resp_labels, m, elapsed_time, iter_num )
            all_scores += [eval_scores]
        print("Finish GaussianMixtureMod2/Mahalanobis : ",m," : ",resp_type )
    else:
        print("Skip GaussianMixtureMod2/Mahalanobis for :",m )
 
    # Run the GMM-Auto for every th_resp value on current dataset (using intersect)- Last tested on 27.01.2021
    #     for resp_type in resp_type_val:
    #         gmm_cluster_mod3 = GaussianMixtureMod3(n_components=n_classes, init_params='random', means_init=es_means_init, covariance_type=cov_type, max_iter=20, random_state=0, resp_type=resp_type )
    #         t.tic() # Start timer
    #         gmm_cluster_mod3.fit(X_train)
    #         elapsed_time = t.tocvalue() #Save elapsed time
    #         iter_num = gmm_cluster_mod3.n_iter_     
    #         resp_labels = "GMM_Auto-"+str(resp_type)
    #         y_train_pred_mod3 = gmm_cluster_mod3.predict(X_train)
    #         eval_scores = cluster_eval(y_train, y_train_pred_mod3, X_train, resp_labels,m, elapsed_time, iter_num)
    #         all_scores += [eval_scores]
    #     print("Finish GaussianMixtureMod3 : ", m," : ",resp_type )

#     #Run the GMM-Auto-v2 for every th_resp value on current dataset (using weights*cv or cv/2) - Last tested on 27.01.2021
#     for resp_type in resp_type_val:
#         gmm_cluster_mod4 = GaussianMixtureMod4(n_components=n_classes, init_params='random', means_init=es_means_init, covariance_type=cov_type, max_iter=20, random_state=0, resp_type=resp_type )
#         t.tic() # Start timer
#         gmm_cluster_mod4.fit(X_train)
#         elapsed_time = t.tocvalue() #Save elapsed time
#         iter_num = gmm_cluster_mod4.n_iter_     
#         resp_labels = "resp Mixing Coefficients -"+str(resp_type)
#         y_train_pred_mod4 = gmm_cluster_mod4.predict(X_train)
#         eval_scores = cluster_eval(y_train, y_train_pred_mod4, X_train, resp_labels,m, elapsed_time, iter_num)
#         all_scores += [eval_scores]
#     print("Finish GaussianMixtureMod4/resp Mixing Coefficients  : ", m, " : ",resp_type )

#     #Run the GMM-Auto-v2 for every th_resp value on current dataset (using resp center values) - Last tested on 27.01.2021
#     for resp_type in resp_type_val:
#         gmm_cluster_mod5 = GaussianMixtureMod5(n_components=n_classes, init_params='random', means_init=es_means_init, covariance_type=cov_type, max_iter=20, random_state=0, resp_type=resp_type )
#         t.tic() # Start timer
#         gmm_cluster_mod5.fit(X_train)
#         elapsed_time = t.tocvalue() #Save elapsed time
#         iter_num = gmm_cluster_mod5.n_iter_     
#         resp_labels = "resp center values-"+str(resp_type)
#         y_train_pred_mod5 = gmm_cluster_mod5.predict(X_train)
#         eval_scores = cluster_eval(y_train, y_train_pred_mod5, X_train, resp_labels,m, elapsed_time, iter_num)
#         all_scores += [eval_scores]
#     print("Finish GaussianMixtureMod5/resp center values : ", m, " : ",resp_type )

#     #Run the GMM-OR for every th_resp value on current dataset
#     for resp_type in resp_type_val:
#         for th_resp in th_resp_val:
#             gmm_cluster_mod = GaussianMixtureMod(n_components=n_classes, init_params='random', means_init=es_means_init, covariance_type=cov_type, max_iter=20, random_state=0, th_resp=th_resp, resp_type=resp_type )

#             t.tic() # Start timer
#             gmm_cluster_mod.fit(X_train)
#             elapsed_time = t.tocvalue() #Save elapsed time
#             iter_num = gmm_cluster_mod.n_iter_       
#             y_train_pred_mod = gmm_cluster_mod.predict(X_train)
#             th_resp_labels = "GMM-"+str(resp_type)+"_th_resp="+str(th_resp)
#     #         print(th_resp_labels," time : ", elapsed_time )   
#             eval_scores = cluster_eval(y_train, y_train_pred_mod, X_train, th_resp_labels,m, elapsed_time, iter_num)
#             all_scores += [eval_scores]

    #Change result to Pandas DataFrame
    result = pd.DataFrame(all_scores)
    all_result = all_result.append(result)
#     print("Finish GaussianMixtureMod : ", m, " : ",resp_type )
all_result = all_result.append(pd.Series(), ignore_index=True) 
all_result.columns=result_labels    


#Save results to Excel
ts = time.time() 
st = datetime.datetime.fromtimestamp(ts).strftime('%H-%M-%S---%d-%m-%Y')
# all_result.to_excel("result/All_result_"+st+".xlsx", index=False)
all_result.to_excel("result/All_result_"+cov_type+"_"+st+".xlsx", index=False)
print("\nFinish at ",st)


In [ ]:
# #Display full output
# from IPython.core.interactiveshell import InteractiveShell
# InteractiveShell.ast_node_interactivity = "all"
from tqdm.auto import tqdm, trange
from ipywidgets import IntProgress
from IPython.display import display
from IPython.core.display import display, HTML
display(HTML("<style>div.output_scroll { height: 40em; }</style>"))

import warnings
warnings.filterwarnings('ignore')
import datetime
import time
from pytictoc import TicToc
import sys
import numpy as np
import pandas as pd
from sklearn.cluster import KMeans, MeanShift
from fcmeans import FCM
from sklearn.mixture import GaussianMixture
from sklearn.mixture_mod import GaussianMixtureMod
from sklearn.mixture_mod2 import GaussianMixtureMod2
from sklearn.mixture_mod3 import GaussianMixtureMod3
from sklearn.mixture_mod4 import GaussianMixtureMod4
from sklearn.mixture_mod5 import GaussianMixtureMod5
from IPython.utils import io
import numpy as np
from sklearn import metrics
from scipy.optimize import linear_sum_assignment
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, adjusted_rand_score, normalized_mutual_info_score, homogeneity_completeness_v_measure,fowlkes_mallows_score,silhouette_score
from sklearn.metrics import davies_bouldin_score, v_measure_score

#Funtion declaration
def cluster_accuracy(y_true, y_pred):
    # compute contingency matrix (also called confusion matrix)
    contingency_matrix = metrics.cluster.contingency_matrix(y_true, y_pred)
#     print("\ncontingency_matrix : \n", contingency_matrix)

    # Find optimal one-to-one mapping between cluster labels and true labels
    row_ind, col_ind = linear_sum_assignment(-contingency_matrix)
    print("row_ind : ", row_ind)
    print("col_ind : ", col_ind)
    val1 = contingency_matrix[row_ind, col_ind].sum()
    print("contingency_matrix[row_ind, col_ind].sum() : ", val1)
    val2 = np.sum(contingency_matrix)
    print("np.sum(contingency_matrix) : ", val2)

    # Return cluster accuracy
    return contingency_matrix[row_ind, col_ind].sum() / np.sum(contingency_matrix)

def purity_score(y_true, y_pred):
    # compute contingency matrix (also called confusion matrix)
    contingency_matrix = metrics.cluster.contingency_matrix(y_true, y_pred)
#     print("\ncontingency_matrix : \n", contingency_matrix)
    
    # return purity
    return np.sum(np.amax(contingency_matrix, axis=0)) / np.sum(contingency_matrix) 

#Get the Clustering Algorithm Performance
def cluster_eval(y_true, y_pred, X_train, cluster_label, m, elapsed_time,iter_num):
    eval_scores = []
    
    accuracy = np.mean(y_pred.ravel() == y_true.ravel()) * 100
    purity = purity_score(y_train, y_pred)
    micro_f1_score = f1_score(y_true, y_pred, average='micro')
    macro_f1_score = f1_score(y_true, y_pred, average='macro')
    weighted_f1_score = f1_score(y_true, y_pred, average='weighted')
    ari_score = adjusted_rand_score(y_true, y_pred)
    nmi_score = normalized_mutual_info_score(y_true, y_pred)
#     hc_v_measure = homogeneity_completeness_v_measure(y_true, y_pred)
    v_measure = v_measure_score(y_true, y_pred)
    fm_score = fowlkes_mallows_score(y_true, y_pred)
#     s_score = silhouette_score(X_train, y_pred, metric='euclidean')
#     db_score = davies_bouldin_score(X_train, y_pred)
    eval_scores = [m, cluster_label, elapsed_time, iter_num, accuracy, purity, micro_f1_score, macro_f1_score, weighted_f1_score, ari_score, 
                   nmi_score, v_measure, fm_score]
    return eval_scores
    
"""------------------------------------------------------------------------------------------------------------------------
#Main Program - Start here!
------------------------------------------------------------------------------------------------------------------------"""
# np.set_printoptions(threshold=sys.maxsize)
# pd.set_option('display.max_rows', dataset.shape[0]+1)

#Define dataset_labels
dataset_labels = ["iris"]
# dataset_labels = ["heartDisease",  "transfusion", "wilt", "balanceScale","dermatology"]  
# dataset_labels = ["heartDisease", "transfusion", "wilt", "breastCancer", "chess", 
#                   "parkinson","australian", "german", "japanese", "iris", "abalone", "wallRobot",
#                   "dermatology","creditApproval", "letters", "eegEyeState",
#                   "seismicBumps","bank", "adultIncome", "sensorlessDrive"]
#Final dataset tested on 11.03.2021
# dataset_labels = ["transfusion", "wilt", "breastCancer", "heartDisease", "eegEyeState", "adultIncome",
#                   "australian", "japanese", "bank", "seismicBumps", "german", "chess", 
#                   "iris", "abalone", "wallRobot", "dermatology"]
# dataset_labels = ["seismicBumps","bank", "adultIncome"]
# skip_Mahal = ["seismicBumps","bank", "adultIncome"]
skip_Mahal = ["seismicBumps","bank"]
# Threshold of GMM-EM Response values
th_resp_val = [0.1, 0.2, 0.3, 0.4, 0.5]
# th_resp_val = [1]

# resp_type_val = ['donate']
# resp_type_val = ['donate']
resp_type_val = ['remove', 'donate']

result_labels = ["Dataset","Algorithm", "Elapsed Time", "Iter_num","accuracy", "purity", "micro_f1_score", "macro_f1_score", "weighted_f1_score", "ari_score", 
                "nmi_score", "hc_v_measure", "fm_score"]

all_scores = []
final_scores = []
all_result = pd.DataFrame()
t = TicToc() # create TicToc instance
# for m in dataset_labels:
for m in tqdm(dataset_labels):
#     enablePrint()
    print("\n\nStart Dataset : ",m)
    #Read dataset
    dataset = pd.read_csv("dataset/"+m+".csv")

    #Drop Target Column in data using Index
    X_train = dataset.drop('Target',axis=1)

    # #How to get Target data
    y_train =  dataset['Target']
    
    print(np.array(y_train))

    n_classes = len(np.unique(y_train))
#     cov_type = 'full'
    cov_type = 'tied'
    
    #Since we have class labels for the training data, we can initialize the GMM parameters in a supervised manner.
    es_means_init = np.array([X_train[y_train == i].mean(axis=0) for i in range(n_classes)])
    
import warnings
warnings.filterwarnings('ignore')
import datetime
import time
from pytictoc import TicToc
import sys
import numpy as np
import pandas as pd
from sklearn.cluster import KMeans, MeanShift    print("es_means_init : \n", es_means_init)

## Find means_init

In [ ]:
import warnings
warnings.filterwarnings('ignore')
import datetime
import time
from pytictoc import TicToc
import sys
import numpy as np
import pandas as pd
from sklearn.cluster import KMeans, MeanShift
from sklearn.mixture import GaussianMixture

dataset_labels = ["iris"]
init_params = 'gmm'

n_components = len(np.unique(y_train))
random_state=0

for m in tqdm(dataset_labels):
    print("\n\nStart Dataset : ",m)
    
    #Read dataset
    dataset = pd.read_csv("dataset/"+m+".csv")

    #Drop Target Column in data using Index
    X_train = dataset.drop('Target',axis=1)

    # #How to get Target data
    y_train =  dataset['Target']

   
    X = X_train
    
    n_samples, n_attributes = X.shape
    
#     print(n_attributes)
    
    df_X = pd.DataFrame(X)
    
    #Find rows average
    df_X['mean'] = df_X.mean(axis=1)
     
    
    #Find Max, Min, Diff, Dev
    Max = max(df_X['mean'])
    Min = min(df_X['mean'])
    
    diff = Max - Min
    dev = diff/n_components
    
    print('Max: ', Max , 'Min: ', Min)   
    print('dev :', dev)
    
    cluster_range = np.zeros((n_components, 2))
    for i in range (n_components):
        cluster_range[i] = Min, Min+dev
        
        Min = Min+dev
        df_X['c'+str(i)]=0
#     print(cluster_range)  

    for j in range (n_components):
        df_X['c'+str(j)][(df_X['mean']>= cluster_range[j,0]) & (df_X['mean'] < cluster_range[j,1])] = 1
    
   
    es_init_means = np.zeros((n_components, n_attributes))
    for k in range (n_components):    
        temp_df_X = df_X.iloc[:, 0:n_attributes][df_X['c'+str(k)] == 1]   
        es_init_means[k] = temp_df_X.mean(axis=0)
        
#         print('es_init_means[',k,'] : ',es_init_means[k])
    print("es_init_means : \n", es_init_means)  
    


In [ ]:

#     if init_params == 'kmeans':
#         resp = np.zeros((n_samples, n_components))
#         label = KMeans(n_clusters= n_components, n_init=1,
#                                random_state=random_state).fit(X).labels_
#         resp[np.arange(n_samples), label] = 1
#         print('label : ', label)
#         print('resp  :  \n', resp)
    
#     elif init_params == 'gmm':
#         resp = np.zeros((n_samples, n_components))
#         gmm_cluster = GaussianMixture(n_components= n_components,  init_params='random', random_state=random_state).fit(X)
#         label = gmm_cluster.predict(X)
#         resp[np.arange(n_samples), label] = 1
#         print('label : ', label)
#         print('resp  :  \n', resp)
        
#     elif init_params == 'random':
#         resp = random_state.rand(n_samples, n_components)
#         resp /= resp.sum(axis=1)[:, np.newaxis]
#         resp1_ = resp
#     else:
#         raise ValueError("Unimplemented initialization method '%s'"
#                      % self.init_params)

    es_means_init = np.array ([[5.005555556, 3.344444444, 1.596296296, 0.303703704],
                                [5.973333333, 2.775, 4.503333333, 1.468333333],
                                [6.86, 3.077142857, 5.731428571, 2.091428571]]) 

In [ ]:
print(df_X)
df_X_new = df_X.iloc[:, 0:n_attributes]
print(df_X_new)

In [ ]:
# print(n_components)
Min = 2.1
dev = 1
Max=5.1
cluster_range = np.zeros((n_components, 2))
for i in range (n_components):
    print(i, Min)
#     cluster_range[i] = i, i+1
    cluster_range[i] = Min, Min+dev
#     min_range[i] = i+1
# #     max_range[i] = Min+dev
    Min = Min+dev
print(cluster_range)
#     print(Min)

In [ ]:
print(max(df_X['mean']))   
print(min(df_X['mean'])) 
print

In [ ]:
cv = np.array([[0.10605892, 0.27159891, 0.53311513, 0.29504658, 0.43389628],
 [0.10532298, 0.30813951, 0.53196672, 0.35493489, 0.52814269]])


o_cv = np.amax(cv, axis=1)
# cv = np.asarray(cv, dtype=np.int32)
print(o_cv)
for i in range (len(o_cv)):
    print(i,"o_cv:",o_cv[i])
    cv = o_cv[i]
    print(i,"cv :",cv)
    
    

In [ ]:
dataset_labels = ["heartDisease", "transfusion", "wilt", "breastCancer", "chess", 
                  "parkinson","australian", "german", "japanese", "iris", "abalone", "wallRobot"
                  "dermatology","creditApproval", "letters", "eegEyeState",
                  "seismicBumps","bank", "adultIncome", "sensorlessDrive", "creditCard"]

skip_Mahal = ["seismicBumps","bank", "adultIncome", "sensorlessDrive", "creditCard"]

for m in tqdm(dataset_labels):
    if m not in (skip_Mahal):
        print("Run Mahalanobis for :",m )
    else:
        print("Skip Mahalanobis for :",m )


In [ ]:
# print(all_result)
all_result = all_result.append(pd.Series(), ignore_index=True) 
all_result.columns=result_labels 

#Save results to Excel
ts = time.time() 
st = datetime.datetime.fromtimestamp(ts).strftime('%H-%M-%S---%d-%m-%Y')
print(st)
all_result.to_excel("result/All_result_"+cov_type+"_"+st+".xlsx", index=False)